In [1]:
import pandas as pd
from summarizer import Summarizer
bert_model = Summarizer()
import warnings
warnings.filterwarnings("ignore")
pd.options.display.max_columns = 999

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [2]:
reviews = pd.read_csv("SecurityDevices_Full.csv")
reviews.head()

User Name Device_Name                                   Raw_Review_Title  \
0     Haley   BlinkMini                                    One major flaw.   
1       Ben   BlinkMini  UPDATED: Confusing cloud storage policy on the...   
2     Wcouv   BlinkMini  Great cameras - Rushed app that is missing key...   
3     Grant   BlinkMini                        Still missing key features!   
4     Grant   BlinkMini   NOT FOR HOME SECURITY!!!!!!!!! (Updated 5/12/20)   

                                     Raw_Review_Text  \
0    I bought this to use as a baby monitor, thin...   
1    UPDATED: When I saw these smaller cameras an...   
2    I pre-ordered 4 cameras without any reviews ...   
3                      The media could not be loa...   
4                      The media could not be loa...   

                                Cleaned_Review_Title  \
0                                     one major flaw   
1  updated confusing cloud storage policy smaller...   
2  great camera rushed app missing key feature cl...   
3                          still missing key feature   
4                        home security updated 51220   

                                 Cleaned_Review_Text                Star  \
0  bought use baby monitor thinking quality good ...  2.0 out of 5 stars   
1  updated saw smaller camera announced excited l...  4.0 out of 5 stars   
2  preordered 4 camera without review posted hope...  3.0 out of 5 stars   
3  medium could loaded may 2021 update unfortunat...  2.0 out of 5 stars   
4  medium could loaded update 51220 3 star 2 came...  2.0 out of 5 stars   

                                Review posted time  \
0  Reviewed in the United States on April 18, 2020   
1  Reviewed in the United States on April 17, 2020   
2  Reviewed in the United States on April 17, 2020   
3  Reviewed in the United States on April 17, 2020   
4  Reviewed in the United States on April 28, 2020   

                                   Total_Description  ReviewDescription_score  \
0  bought use baby monitor thinking quality good ...                 0.996147   
1  updated saw smaller camera announced excited l...                 0.993361   
2  preordered 4 camera without review posted hope...                 0.997422   
3  medium could loaded may 2021 update unfortunat...                 0.995359   
4  medium could loaded update 51220 3 star 2 came...                 0.993834   

  ReviewDescription_Sentiment  
0                    NEGATIVE  
1                    NEGATIVE  
2                    NEGATIVE  
3                    NEGATIVE  
4                    NEGATIVE

In [3]:
reviews.shape

(23492, 11)

In [4]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
reviews["sentiment"] = le.fit_transform(reviews["ReviewDescription_Sentiment"])
reviews.head()

User Name Device_Name                                   Raw_Review_Title  \
0     Haley   BlinkMini                                    One major flaw.   
1       Ben   BlinkMini  UPDATED: Confusing cloud storage policy on the...   
2     Wcouv   BlinkMini  Great cameras - Rushed app that is missing key...   
3     Grant   BlinkMini                        Still missing key features!   
4     Grant   BlinkMini   NOT FOR HOME SECURITY!!!!!!!!! (Updated 5/12/20)   

                                     Raw_Review_Text  \
0    I bought this to use as a baby monitor, thin...   
1    UPDATED: When I saw these smaller cameras an...   
2    I pre-ordered 4 cameras without any reviews ...   
3                      The media could not be loa...   
4                      The media could not be loa...   

                                Cleaned_Review_Title  \
0                                     one major flaw   
1  updated confusing cloud storage policy smaller...   
2  great camera rushed app missing key feature cl...   
3                          still missing key feature   
4                        home security updated 51220   

                                 Cleaned_Review_Text                Star  \
0  bought use baby monitor thinking quality good ...  2.0 out of 5 stars   
1  updated saw smaller camera announced excited l...  4.0 out of 5 stars   
2  preordered 4 camera without review posted hope...  3.0 out of 5 stars   
3  medium could loaded may 2021 update unfortunat...  2.0 out of 5 stars   
4  medium could loaded update 51220 3 star 2 came...  2.0 out of 5 stars   

                                Review posted time  \
0  Reviewed in the United States on April 18, 2020   
1  Reviewed in the United States on April 17, 2020   
2  Reviewed in the United States on April 17, 2020   
3  Reviewed in the United States on April 17, 2020   
4  Reviewed in the United States on April 28, 2020   

                                   Total_Description  ReviewDescription_score  \
0  bought use baby monitor thinking quality good ...                 0.996147   
1  updated saw smaller camera announced excited l...                 0.993361   
2  preordered 4 camera without review posted hope...                 0.997422   
3  medium could loaded may 2021 update unfortunat...                 0.995359   
4  medium could loaded update 51220 3 star 2 came...                 0.993834   

  ReviewDescription_Sentiment  sentiment  
0                    NEGATIVE          0  
1                    NEGATIVE          0  
2                    NEGATIVE          0  
3                    NEGATIVE          0  
4                    NEGATIVE          0

## Preprocessing

**Removing Special Characters**

In [5]:
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer,PorterStemmer
from nltk.corpus import stopwords
import re
lemmatizer = WordNetLemmatizer()
stemmer = PorterStemmer() 

def preprocess(sentence):
    sentence=str(sentence)
    sentence = sentence.lower()
    sentence=sentence.replace('{html}',"") 
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', sentence)
    rem_url=re.sub(r'http\S+', '',cleantext)
    rem_num = re.sub('[0-9]+', '', rem_url)
    rem_alp = re.sub("[^ .,!A-Za-z0-9]","", rem_num)
    rem_nextline = re.sub('\\n', '', rem_alp)#removing the '\n' character
    tokenizer = RegexpTokenizer(r'\w+')
    tokens = tokenizer.tokenize(rem_nextline)  
    #filtered_words = [w for w in tokens if len(w) > 2 if not w in stopwords.words('english')]
    #stem_words=[stemmer.stem(w) for w in filtered_words]
    #lemma_words=[lemmatizer.lemmatize(w) for w in stem_words]
    return "".join(rem_nextline)

**Removing Emojis**

In [6]:
import re
def remove_emojis(data):
    emoj = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)
    return re.sub(emoj, '', data)

**Contraction Mapping**

In [7]:
contraction_mapping = {"ain't": "is not", "&": "and", "aren't": "are not","can't": "cannot", "'cause": "because", "could've": "could have", "couldn't": "could not",

                           "didn't": "did not", "doesn't": "does not", "don't": "do not", "hadn't": "had not", "hasn't": "has not", "haven't": "have not",

                           "he'd": "he would","he'll": "he will", "he's": "he is", "how'd": "how did", "how'd'y": "how do you", "how'll": "how will", "how's": "how is",

                           "I'd": "I would", "I'd've": "I would have", "I'll": "I will", "I'll've": "I will have","I'm": "I am", "I've": "I have", "i'd": "i would",

                           "i'd've": "i would have", "i'll": "i will",  "i'll've": "i will have","i'm": "i am", "i've": "i have", "isn't": "is not", "it'd": "it would",

                           "it'd've": "it would have", "it'll": "it will", "it'll've": "it will have","it's": "it is", "let's": "let us", "ma'am": "madam",

                           "mayn't": "may not", "might've": "might have","mightn't": "might not","mightn't've": "might not have", "must've": "must have",

                           "mustn't": "must not", "mustn't've": "must not have", "needn't": "need not", "needn't've": "need not have","o'clock": "of the clock",

                           "oughtn't": "ought not", "oughtn't've": "ought not have", "shan't": "shall not", "sha'n't": "shall not", "shan't've": "shall not have",

                           "she'd": "she would", "she'd've": "she would have", "she'll": "she will", "she'll've": "she will have", "she's": "she is",

                           "should've": "should have", "shouldn't": "should not", "shouldn't've": "should not have", "so've": "so have","so's": "so as",

                           "this's": "this is","that'd": "that would", "that'd've": "that would have", "that's": "that is", "there'd": "there would",

                           "there'd've": "there would have", "there's": "there is", "here's": "here is","they'd": "they would", "they'd've": "they would have",

                           "they'll": "they will", "they'll've": "they will have", "they're": "they are", "they've": "they have", "to've": "to have",

                           "wasn't": "was not", "we'd": "we would", "we'd've": "we would have", "we'll": "we will", "we'll've": "we will have", "we're": "we are",

                           "we've": "we have", "weren't": "were not", "what'll": "what will", "what'll've": "what will have", "what're": "what are",

                           "what's": "what is", "what've": "what have", "when's": "when is", "when've": "when have", "where'd": "where did", "where's": "where is",

                           "where've": "where have", "who'll": "who will", "who'll've": "who will have", "who's": "who is", "who've": "who have",

                           "why's": "why is", "why've": "why have", "will've": "will have", "won't": "will not", "won't've": "will not have",

                           "would've": "would have", "wouldn't": "would not", "wouldn't've": "would not have", "y'all": "you all",

                           "y'all'd": "you all would","y'all'd've": "you all would have","y'all're": "you all are","y'all've": "you all have",

                           "you'd": "you would", "you'd've": "you would have", "you'll": "you will", "you'll've": "you will have",

                           "you're": "you are", "you've": "you have"}

## Text Summarizing the Positive sentiment BlinkMini reviews

In [15]:
data_blinkmini_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'BlinkMini') ]
data_blinkmini_pos.head()

User Name Device_Name                     Raw_Review_Title  \
7       Johnny   BlinkMini     Easy to install only took 5 min!   
17  Chris Shaw   BlinkMini  Easy set up and great image quality   
26          HG   BlinkMini              Simple, fun, works well   
44       Ed122   BlinkMini                    Great Cat Monitor   
47       Jeily   BlinkMini                  Amazing tiny camera   

                                      Raw_Review_Text  \
7     I love this lil camera!! Easy to install! On...   
17    This is a great little camera monitor. Pros:...   
26                      The media could not be loa...   
44                      The media could not be loa...   
47    I just got the new blink mini x 2.  I have b...   

            Cleaned_Review_Title  \
7        easy install took 5 min   
17  easy set great image quality   
26          simple fun work well   
44             great cat monitor   
47           amazing tiny camera   

                                  Cleaned_Review_Text                Star  \
7   love lil camera easy install took 5 min work g...  5.0 out of 5 stars   
17  great little camera monitor pro easy set easil...  5.0 out of 5 stars   
26  medium could loaded happy purchase feel like w...  5.0 out of 5 stars   
44  medium could loaded love new blink mini 30 thi...  5.0 out of 5 stars   
47  got new blink mini x 2 using day currently 10 ...  5.0 out of 5 stars   

                                   Review posted time  \
7     Reviewed in the United States on April 17, 2020   
17      Reviewed in the United States on June 5, 2020   
26  Reviewed in the United States on October 26, 2020   
44     Reviewed in the United States on July 27, 2020   
47    Reviewed in the United States on April 18, 2020   

                                    Total_Description  \
7   love lil camera easy install took 5 min work g...   
17  great little camera monitor pro easy set easil...   
26  medium could loaded happy purchase feel like w...   
44  medium could loaded love new blink mini 30 thi...   
47  got new blink mini x 2 using day currently 10 ...   

    ReviewDescription_score ReviewDescription_Sentiment  sentiment  
7                  0.635002                    POSITIVE          1  
17                 0.690023                    POSITIVE          1  
26                 0.975907                    POSITIVE          1  
44                 0.875019                    POSITIVE          1  
47                 0.948171                    POSITIVE          1

In [16]:
data_blinkmini_pos_list = data_blinkmini_pos["Raw_Review_Text"].values.tolist()

blinkmini_pos_reviews = ' '.join([str(item) for item in data_blinkmini_pos_list])

newString = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in blinkmini_pos_reviews.split(" ")])
blinkmini_pos_reviews = preprocess(blinkmini_pos_reviews)
blinkmini_pos_reviews = remove_emojis(blinkmini_pos_reviews)
blinkmini_pos_reviews

'  i love this lil camera!! easy to install! only took  min and it works great!! highly recommend this!!   this is a great little camera monitor. pros easy set up, easily managed with your smart phone, clear image quality with motion detection. can be set up to arm and record at any time. i bought this to use in my master bedroom by my desk where i keep sensitive information.cons if you are using it with another blink product and you arm  then the other blink unit also needs to be armed which is an issue because my other unit uses  aa batteries. there is no timer on the app to set up a time to arm which would by useful because i sometimes forget to arm at night. it has good night vision quality. it needs to be plugged in so is a problem if you put it in a place i.e. bedroom closet if there is no outlet. because of this, it is difficult to make the camera more hidden if you are looking for a nanny camera for example.overall it is easy to use and i would recommend it for a basic home sec

In [22]:
bert_model = Summarizer()
bert_summary_blinkmini_pos = ''.join(bert_model(blinkmini_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all BlinkMini positive reviews is: \n\n\n", bert_summary_blinkmini_pos)

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).



 Text summarization of the all BlinkMini positive reviews is: 


 only took  min and it works great!! easy to set up and use because they use the same app as the blink xt cameras. when it does work, the motion detection is highly sensitive and we get immediate alerts. i will say, it is very good about picking up voice and audio! i have mine in the windowsill facing out so maybe the netting over the window makes it bad also it doesnt always go off for motion detection. we had intended to use it as a baby monitor but it has a very obnoxious clicking sound every time you turn on and off the live view. even in night vision mode the camera is better than more expensive cameras ive purchased. this small camera is mighty, excellent picture and coverage, i put it in my garage and i can see both the rear and front entrance leading into my interior door. the sound is also excellent and clear. but the black and white at night is still perfectly able to spot shadow people walking around your thin

## Text Summarizing the Negative sentiment BlinkMini reviews

In [36]:
data_blinkmini_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'BlinkMini') ]
data_blinkmini_neg = data_blinkmini_neg.head(1000)

In [37]:
data_blinkmini_neg.head()

User Name Device_Name                                   Raw_Review_Title  \
0     Haley   BlinkMini                                    One major flaw.   
1       Ben   BlinkMini  UPDATED: Confusing cloud storage policy on the...   
2     Wcouv   BlinkMini  Great cameras - Rushed app that is missing key...   
3     Grant   BlinkMini                        Still missing key features!   
4     Grant   BlinkMini   NOT FOR HOME SECURITY!!!!!!!!! (Updated 5/12/20)   

                                     Raw_Review_Text  \
0    I bought this to use as a baby monitor, thin...   
1    UPDATED: When I saw these smaller cameras an...   
2    I pre-ordered 4 cameras without any reviews ...   
3                      The media could not be loa...   
4                      The media could not be loa...   

                                Cleaned_Review_Title  \
0                                     one major flaw   
1  updated confusing cloud storage policy smaller...   
2  great camera rushed app missing key feature cl...   
3                          still missing key feature   
4                        home security updated 51220   

                                 Cleaned_Review_Text                Star  \
0  bought use baby monitor thinking quality good ...  2.0 out of 5 stars   
1  updated saw smaller camera announced excited l...  4.0 out of 5 stars   
2  preordered 4 camera without review posted hope...  3.0 out of 5 stars   
3  medium could loaded may 2021 update unfortunat...  2.0 out of 5 stars   
4  medium could loaded update 51220 3 star 2 came...  2.0 out of 5 stars   

                                Review posted time  \
0  Reviewed in the United States on April 18, 2020   
1  Reviewed in the United States on April 17, 2020   
2  Reviewed in the United States on April 17, 2020   
3  Reviewed in the United States on April 17, 2020   
4  Reviewed in the United States on April 28, 2020   

                                   Total_Description  ReviewDescription_score  \
0  bought use baby monitor thinking quality good ...                 0.996147   
1  updated saw smaller camera announced excited l...                 0.993361   
2  preordered 4 camera without review posted hope...                 0.997422   
3  medium could loaded may 2021 update unfortunat...                 0.995359   
4  medium could loaded update 51220 3 star 2 came...                 0.993834   

  ReviewDescription_Sentiment  sentiment  
0                    NEGATIVE          0  
1                    NEGATIVE          0  
2                    NEGATIVE          0  
3                    NEGATIVE          0  
4                    NEGATIVE          0

In [39]:
data_blinkmini_neg_list = data_blinkmini_neg["Raw_Review_Text"].values.tolist()

blinkmini_neg_reviews = ' '.join([str(item) for item in data_blinkmini_neg_list])

blinkmini_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in blinkmini_neg_reviews.split(" ")])
blinkmini_neg_reviews = preprocess(blinkmini_neg_reviews)
blinkmini_neg_reviews = remove_emojis(blinkmini_neg_reviews)
blinkmini_neg_reviews

'  i bought this to use as a baby monitor, thinking if the quality was good i would end up purchasing an outdoor set as well. i got it in this afternoon, and set up was super easy. the picture quality is excellent for the price point.the main issue for me is that there is no option for continuous viewing. the live view from the app will automatically shut off after  seconds if you do not tap the continue prompt. if i had known this ahead of time, i would have never purchased a blink camera. i watch my daughter on a fire tablet while i work at night, and it is really not feasible to stop typing every  seconds to press a button.maybe it is my fault for not realizing it, but i do not remember reading any information about the length of viewing time, so i assumed it would be like the foscam i had sought to replace. if blink ever adds an update for continuous viewing, i would repurchase in a heartbeat, but for now, i am sending it back.   updated when i saw these smaller cameras announced i

In [40]:
bert_summary_blinkmini_neg = ''.join(bert_model(blinkmini_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all BlinkMini negative reviews is: \n\n\n", bert_summary_blinkmini_neg)


 Text summarization of the all BlinkMini negative reviews is: 


 i bought this to use as a baby monitor, thinking if the quality was good i would end up purchasing an outdoor set as well. for years i have been able to see live feeds in a multipane format and select the camera i want to zoom in on that one, not with this app.second, tech support is, at best, not good. i was told after  minutes on the phone again, all of this occurring in the same hour, that they wanted me to reset the camera again because of my internet. its compact and wired so i have it just sitting on the entertainment center to not deal with the wire being in the way. i bought this and stopped using it after one month. also a really big no for me is that they have no options for setting the camera at a permanent zoomed setting. there is a way to save the video clips to your phone and i know how to do this now, so thats what i do.overall the downside is just my fault, not the apps fault. days into it, i am really n

## Text Summarizing the Positive sentiment Blink Video reviews

In [42]:
data_blinkvideo_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'Blink Video') ]
data_blinkvideo_pos.head()

User Name  Device_Name                        Raw_Review_Title  \
5005        dschott  Blink Video                             Works well!   
5027      JCReviews  Blink Video                          So far so good   
5083           Andi  Blink Video  Excellent, affordable door bell camera   
5094   L. E. Carter  Blink Video                Works great easy install   
5098  J. Gallaugher  Blink Video                    Blink doorbell is ok   

                                        Raw_Review_Text  \
5005    I got this doorbell because itâ€™s cheaper t...   
5027                      The media could not be loa...   
5083    The quality and functionality of the blink c...   
5094    Just got product delivered today so I canâ€™...   
5098    I feel like it should do more. It works fine...   

                       Cleaned_Review_Title  \
5005                              work well   
5027                               far good   
5083  excellent affordable door bell camera   
5094                work great easy install   
5098                      blink doorbell ok   

                                    Cleaned_Review_Text                Star  \
5005  got doorbell cheaper ring one easy set two scr...  5.0 out of 5 stars   
5027  medium could loaded received item yesterday ab...  5.0 out of 5 stars   
5083  quality functionality blink camera system app ...  5.0 out of 5 stars   
5094  got product delivered today talk owning 3 hour...  5.0 out of 5 stars   
5098  feel like work fine figure echo show automatic...  3.0 out of 5 stars   

                                     Review posted time  \
5005  Reviewed in the United States on October 24, 2021   
5027  Reviewed in the United States on October 26, 2021   
5083  Reviewed in the United States on October 28, 2021   
5094  Reviewed in the United States on October 24, 2021   
5098  Reviewed in the United States on December 8, 2021   

                                      Total_Description  \
5005  got doorbell cheaper ring one easy set two scr...   
5027  medium could loaded received item yesterday ab...   
5083  quality functionality blink camera system app ...   
5094  got product delivered today talk owning 3 hour...   
5098  feel like work fine figure echo show automatic...   

      ReviewDescription_score ReviewDescription_Sentiment  sentiment  
5005                 0.997284                    POSITIVE          1  
5027                 0.997406                    POSITIVE          1  
5083                 0.985342                    POSITIVE          1  
5094                 0.968566                    POSITIVE          1  
5098                 0.925040                    POSITIVE          1

In [43]:
data_blinkvideo_pos_list = data_blinkvideo_pos["Raw_Review_Text"].values.tolist()

blinkvideo_pos_reviews = ' '.join([str(item) for item in data_blinkvideo_pos_list])

blinkvideo_pos_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in blinkvideo_pos_reviews.split(" ")])
blinkvideo_pos_reviews = preprocess(blinkvideo_pos_reviews)
blinkvideo_pos_reviews = remove_emojis(blinkvideo_pos_reviews)
blinkvideo_pos_reviews

'  i got this doorbell because its cheaper than the ring one. it was easy to set up. two screws into the door frame and i was able to slide it on. the camera works well and i was able to link it to all my alexa stuff. i did the no wire worked and it works well!                     the media could not be loaded.                  received this item yesterday. was able to install the doorbell today. fairly easy installation. camera quality is good. i chose this doorbell because of the ability to wire it to my existing chime box in the house. my house was built in the early s and the original chime box is compatible and does ring when the doorbell is activated.got the sync module  combo because i had the original sync module for my outdoor cams and wanted to upgrade to local storage. ordered a sandisk  gb usb drive and works wonderfully with the local storage.if this doorbell cam is anything like the outdoor cameras, i expect the night vision to be good. i tested the microphone and sound q

In [44]:
bert_summary_blinkvideo_pos = ''.join(bert_model(blinkvideo_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Blink Video positive reviews is: \n\n\n", bert_summary_blinkvideo_pos)


 Text summarization of the all Blink Video positive reviews is: 


 i got this doorbell because its cheaper than the ring one. ordered a sandisk  gb usb drive and works wonderfully with the local storage.if this doorbell cam is anything like the outdoor cameras, i expect the night vision to be good. there are instructions in the phone app to assist in mounting the doorbell. absolutely great quality a video and links with the other blink cameras so i suppose this is worth it for me. update  i still love this system. there are  external doors and i never could tell where people were when i heard the old doorbell. once a video file is generated it comes up for viewing the same as my other two blink cameras. overall i love it and i am able to see when my packages come when im not home. works very well and integrates nicely into your alexa you can select what devices ring and view the camera on the alexa show as well as your phone. i am extremely satisfied with this doorbell camera. keep i

## Text Summarizing the Negative sentiment Blink Video reviews

In [8]:
data_blinkvideo_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'Blink Video') ]
data_blinkvideo_neg = data_blinkvideo_neg.head(1000)
data_blinkvideo_neg.head()

User Name  Device_Name  \
5000   Sock My World  Blink Video   
5001   Sock My World  Blink Video   
5002  Whose That Guy  Blink Video   
5003  Whose That Guy  Blink Video   
5004         themike  Blink Video   

                                       Raw_Review_Title  \
5000                  READ THIS BEFORE ANY OTHER REVIEW   
5001  Well worth the cost & perfect add on for exist...   
5002                Potential to be great, but not yet.   
5003              Not sure why all the negative reviews   
5004                         Impressive little doorbell   

                                        Raw_Review_Text  \
5000    I also had an issue with the mount and spent...   
5001                      The media could not be loa...   
5002    A few years ago I was excited to see that BL...   
5003    I got this and just mounted it. I will say t...   
5004    Thereâ€™s a few more steps to set up, and re...   

                                   Cleaned_Review_Title  \
5000                                        read review   
5001  well worth cost perfect add existing blink cus...   
5002                                potential great yet   
5003                               sure negative review   
5004                         impressive little doorbell   

                                    Cleaned_Review_Text                Star  \
5000  also issue mount spent hr trying secure luck t...  4.0 out of 5 stars   
5001  medium could loaded like happy existing blink ...  5.0 out of 5 stars   
5002  year ago excited see blink doorbell announced ...  2.0 out of 5 stars   
5003  got mounted say instruction detailed tech orie...  4.0 out of 5 stars   
5004  step set requires blink sync completely wirele...  5.0 out of 5 stars   

                                     Review posted time  \
5000  Reviewed in the United States on October 23, 2021   
5001  Reviewed in the United States on November 4, 2021   
5002  Reviewed in the United States on October 23, 2021   
5003  Reviewed in the United States on October 24, 2021   
5004  Reviewed in the United States on October 23, 2021   

                                      Total_Description  \
5000  also issue mount spent hr trying secure luck t...   
5001  medium could loaded like happy existing blink ...   
5002  year ago excited see blink doorbell announced ...   
5003  got mounted say instruction detailed tech orie...   
5004  step set requires blink sync completely wirele...   

      ReviewDescription_score ReviewDescription_Sentiment  sentiment  
5000                 0.996094                    NEGATIVE          0  
5001                 0.965762                    NEGATIVE          0  
5002                 0.990444                    NEGATIVE          0  
5003                 0.985659                    NEGATIVE          0  
5004                 0.975019                    NEGATIVE          0

In [9]:
data_blinkvideo_neg_list = data_blinkvideo_neg["Raw_Review_Text"].values.tolist()

blinkvideo_neg_reviews = ' '.join([str(item) for item in data_blinkvideo_neg_list])

blinkvideo_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in blinkvideo_neg_reviews.split(" ")])
blinkvideo_neg_reviews = preprocess(blinkvideo_neg_reviews)
blinkvideo_neg_reviews = remove_emojis(blinkvideo_neg_reviews)
blinkvideo_neg_reviews

'  i also had an issue with the mount and spent an hr trying to secure it on with no luck. i am tech savvy so this thing should not be as hard as it is to simply mount the doorbell to the mount. i just put my return in and was just frustrated all around. to get a new one would take almost a week. i decided to take a breath and a dab. i sat down and closely looked at the backing and the mount. you have to put alot of effort into sliding the mount on. once you closely look at how the inserts go in line it up and push really hard sliding the doorbell down. it will slide and lock into place. it should not be this hard to put on and i can see why people are leaving poor reviews. trust me on this though and do not give up!update day  and so far so good. i have realized the reason for it being so hard to put the mount on, its to make it very sturdy when the doorbell is attached. i have read a review talking about this being easy to steal and i would have to disagree. the door bell is not goin

In [10]:
bert_summary_blinkvideo_neg = ''.join(bert_model(blinkvideo_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Blink Video negative reviews is: \n\n\n", bert_summary_blinkvideo_neg)


 Text summarization of the all Blink Video negative reviews is: 


 i also had an issue with the mount and spent an hr trying to secure it on with no luck. i was worried that it would not work with my wired chime from the old doorbell. just things to keep in mind if you do not have a blink device yet.the doorbell does what it supposed to do. you will have to pull it off the wall if you ever have to scan the code on the back of the doorbell.i tested it on my doorbell wire and received a warning that the voltage was too low. i know for a fact that even wired the doorbell will go dead in  days.i do not know who the genius is on programming and making the doorbell work. as you would imagine alexa integration works fine as well, so alerts and door bell rings can be pushed to your alexa powered devices.now for the bad as i guess you get what you pay for. i do not know what product design was thinking but that backplate you have to press the device on to is something else. this may seem like

## Text Summarizing the Positive sentiment Echo Show reviews

In [8]:
data_echoshow_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'Echo Show') ]
data_echoshow_pos.head()

User Name Device_Name  \
8402   Eric Moyer   Echo Show   
8403   Eric Moyer   Echo Show   
8428    G. Pounds   Echo Show   
8430     JBDragon   Echo Show   
8435  Tim Dobbins   Echo Show   

                                       Raw_Review_Title  \
8402  Echo Show 8: Good But Not Quite as Good as the...   
8403              So easy and so good with Ring cameras   
8428                        Alexa, open Ambient Visions   
8430  Great sound, gets better the more you play wit...   
8435                                 Discount (updated)   

                                        Raw_Review_Text  \
8402    I have had an Echo Show 5 for over a month i...   
8403    I received my new Echo Show 8 - HD 8" smart ...   
8428                      The media could not be loa...   
8430                      The media could not be loa...   
8435    Not very cool, offer a pre-sale for $30 off ...   

                         Cleaned_Review_Title  \
8402  echo show 8 good quite good echo show 5   
8403                    easy good ring camera   
8428                alexa open ambient vision   
8430              great sound get better play   
8435                         discount updated   

                                    Cleaned_Review_Text                Star  \
8402  echo show 5 month work office like great deal ...  4.0 out of 5 stars   
8403  received new echo show 8 hd 8 smart display al...  5.0 out of 5 stars   
8428  medium could loaded already lot read various u...  5.0 out of 5 stars   
8430  medium could loaded bought instead replacing d...  5.0 out of 5 stars   
8435  cool offer presale 30 week later reduce anothe...  5.0 out of 5 stars   

                                     Review posted time  \
8402  Reviewed in the United States on November 26, ...   
8403  Reviewed in the United States on November 26, ...   
8428  Reviewed in the United States on October 11, 2020   
8430  Reviewed in the United States on December 25, ...   
8435  Reviewed in the United States on November 28, ...   

                                      Total_Description  \
8402  echo show 5 month work office like great deal ...   
8403  received new echo show 8 hd 8 smart display al...   
8428  medium could loaded already lot read various u...   
8430  medium could loaded bought instead replacing d...   
8435  cool offer presale 30 week later reduce anothe...   

      ReviewDescription_score ReviewDescription_Sentiment  sentiment  
8402                 0.998272                    POSITIVE          1  
8403                 0.760190                    POSITIVE          1  
8428                 0.989147                    POSITIVE          1  
8430                 0.989075                    POSITIVE          1  
8435                 0.998545                    POSITIVE          1

In [9]:
data_echoshow_pos_list = data_echoshow_pos["Raw_Review_Text"].values.tolist()

echoshow_pos_reviews = ' '.join([str(item) for item in data_echoshow_pos_list])

echoshow_pos_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in echoshow_pos_reviews.split(" ")])
echoshow_pos_reviews = preprocess(echoshow_pos_reviews)
echoshow_pos_reviews = remove_emojis(echoshow_pos_reviews)
echoshow_pos_reviews

'  i have had an echo show  for over a month in my work office and like it a great deal. i especially like the ability to customize the clock.i received the new echo show  as a gift this past weekend and like it for most of the same reasons i like the echo show  great connectivity good diversity of content and skills and great as a sound speaker and photo display.but i found that the es does not have the same options for clock faces as the es. there is no apparent reason for this, nor is it highlighted in the marketing for the es. amazon, please update the es software to permit at least the same range of clockfaces as the es.   i received my new echo show   hd  smart display with alexa a couple hours ago. i had it unpacked and connected to my wifi within  minutes. i have  ring cameras, front door bell, a front and back yard motion light cameras. once i followed the steps to add ring in the alexa app, like  minutes, it was so intuitive i do not know what i did right but another  minutes

In [10]:
bert_summary_echoshow_pos = ''.join(bert_model(echoshow_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Echo Show positive reviews is: \n\n\n", bert_summary_echoshow_pos)


 Text summarization of the all Echo Show positive reviews is: 


 i have had an echo show  for over a month in my work office and like it a great deal. i purchased an echo  as well, which will replace my echo dot in my kitchen where i have less space, but this is about the echo .i am absolutely amazed at the sound quality for starters. i wanted to get the show, so my wife could look at recipes while working in the kitchen, but was not sure if she would like it as she does not like a lot of clutter on the kitchen counters. for frame of reference we have about  echo devices throughout our house, so saying this es is the most responsive device we own does mean something. i choose art for my home screen and really love the beautiful scenes in the screen. only problem i have is that the speaker is in the back, so its louder towards the back than the front looking at the screen. the sound is very good and pretty loud. i wanted another device to be able to add one in my art studio. i have re

## Text Summarizing the Negative sentiment Echo Show reviews

In [14]:
data_echoshow_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'Echo Show') ]
data_echoshow_neg = data_echoshow_neg.head(1000)
data_echoshow_neg.head()

User Name Device_Name  \
8399              Jeff   Echo Show   
8400              Jeff   Echo Show   
8401    Dan Curtis Fan   Echo Show   
8404  Alexander Scherr   Echo Show   
8405    Dave W. Dinges   Echo Show   

                                      Raw_Review_Title  \
8399                     Great, but for one fatal flaw   
8400           Alexa, I don't want any "Things to Try"   
8401                      I thought it would be better   
8404                A Great Addition to Your Home Tech   
8405  Scaled down version of the show 2, but a bargain   

                                        Raw_Review_Text  \
8399    I really do enjoy this device and am impress...   
8400    Aaaaaaaggghhh!  The "Things to Try" sayings ...   
8401    I had the echo 5 and I can't stand the "try ...   
8404    This is my first Echo device.  Had already s...   
8405    I have a bunch of Echo devices in my home. I...   

               Cleaned_Review_Title  \
8399           great one fatal flaw   
8400      alexa dont want thing try   
8401           thought would better   
8404       great addition home tech   
8405  scaled version show 2 bargain   

                                    Cleaned_Review_Text                Star  \
8399  really enjoy device impressed ability alexa sa...  2.0 out of 5 stars   
8400  aaaaaaaggghhh thing try saying sooooooooo anno...  1.0 out of 5 stars   
8401  echo 5 cant stand try alexa phrase bottom revi...  1.0 out of 5 stars   
8404  first echo device already set several skill al...  5.0 out of 5 stars   
8405  bunch echo device home including echo show 2 1...  5.0 out of 5 stars   

                                     Review posted time  \
8399  Reviewed in the United States on November 26, ...   
8400  Reviewed in the United States on November 27, ...   
8401  Reviewed in the United States on November 25, ...   
8404  Reviewed in the United States on November 27, ...   
8405  Reviewed in the United States on November 26, ...   

                                      Total_Description  \
8399  really enjoy device impressed ability alexa sa...   
8400  aaaaaaaggghhh thing try saying sooooooooo anno...   
8401  echo 5 cant stand try alexa phrase bottom revi...   
8404  first echo device already set several skill al...   
8405  bunch echo device home including echo show 2 1...   

      ReviewDescription_score ReviewDescription_Sentiment  sentiment  
8399                 0.878031                    NEGATIVE          0  
8400                 0.998759                    NEGATIVE          0  
8401                 0.997048                    NEGATIVE          0  
8404                 0.964135                    NEGATIVE          0  
8405                 0.986055                    NEGATIVE          0

In [15]:
data_echoshow_neg_list = data_echoshow_neg["Raw_Review_Text"].values.tolist()

echoshow_neg_reviews = ' '.join([str(item) for item in data_echoshow_neg_list])

echoshow_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in echoshow_neg_reviews.split(" ")])
echoshow_neg_reviews = preprocess(echoshow_neg_reviews)
echoshow_neg_reviews = remove_emojis(echoshow_neg_reviews)
echoshow_neg_reviews

'  i really do enjoy this device and am impressed at the abilities of alexa. that said, until they add the option to disable the try alexa suggestions on the bottom of the home screen i cant recommend it and will not be buying addition units.looking online i am far from the only person driven crazy by this so i hope amazon listens to the feedback and makes this possible in a future update.edit the current top review claims that i and everyone else complaining about this am wrong and this can be disabled. while this person is right in the fact you can customize a lot of the display, the try suggestions at the bottom are not one of them. for the record i contacted amazon support before posting my review to confirm this. anyone who says otherwise is simply wrong.   aaaaaaaggghhh!  the things to try sayings are sooooooooo annoying.  and they are so stupid and do not pertain to me at all.  alexa, how do you say hello in german, alexa, rap for me., alexa, how hot is the sun, alexa, what is t

In [16]:
bert_summary_echoshow_neg = ''.join(bert_model(echoshow_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Echo Show negative reviews is: \n\n\n", bert_summary_echoshow_neg)


 Text summarization of the all Echo Show negative reviews is: 


 i really do enjoy this device and am impressed at the abilities of alexa. anywhere else i feel it would not be put into use enough to be worth the cost.also, i advise everyone to take a look at the google nest hub, lenovo and the rest of the echo show smart system. the bad news is, do i really want to keep it  i really like the large clock face on the show and it seems ridiculous i have no clock options on the show. no, the mac address that i am showing does not match my actual mac address, i changed it, so as not to be stupid in a public showing. i love the fact that i can create a slideshow of family pictures that plays on the show when its not in use. alexa is just plain stupid, i own  echo dots rev  ,  echos show  and echo auto. i was worried the screen would be small like the echo show , but it is as large as our original, boxy show.i keep it in the kitchen to play music and it sounds fine. i will be removing it fr

## Text Summarizing the Positive sentiment McAfee reviews

In [17]:
data_mcafee_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'McAfee') ]
data_mcafee_pos.head()

User Name Device_Name  \
13452          Dreamer      McAfee   
13461    Ron Fleischer      McAfee   
13485      Luis Rosado      McAfee   
13518  Kindle Customer      McAfee   
13531            Michi      McAfee   

                                        Raw_Review_Title  \
13452                 It always had been a great product   
13461                                          Great buy   
13485       The additional features make it a good value   
13518  Good product and great support from mcafee and...   
13531                                       Works great!   

                                         Raw_Review_Text  \
13452    There are 2 things you should be aware of wh...   
13461    Great product and McAfee customer service is...   
13485    Well worth the 24 bucks I paid! Comes with a...   
13518    I have been  using mcafee for about 5 year a...   
13531    I had an issue loading it on my old Toshiba ...   

                           Cleaned_Review_Title  \
13452                      always great product   
13461                                 great buy   
13485        additional feature make good value   
13518  good product great support mcafee amazon   
13531                                work great   

                                     Cleaned_Review_Text                Star  \
13452  2 thing aware purchasing mcafee total protecti...  5.0 out of 5 stars   
13461  great product mcafee customer service helpful ...  5.0 out of 5 stars   
13485  well worth 24 buck paid come password manager ...  5.0 out of 5 stars   
13518  using mcafee 5 year say best antivirus ever us...  5.0 out of 5 stars   
13531  issue loading old toshiba pc software update n...  5.0 out of 5 stars   

                                      Review posted time  \
13452  Reviewed in the United States on December 17, ...   
13461  Reviewed in the United States on November 22, ...   
13485    Reviewed in the United States on April 23, 2021   
13518  Reviewed in the United States on February 15, ...   
13531  Reviewed in the United States on February 25, ...   

                                       Total_Description  \
13452  2 thing aware purchasing mcafee total protecti...   
13461  great product mcafee customer service helpful ...   
13485  well worth 24 buck paid come password manager ...   
13518  using mcafee 5 year say best antivirus ever us...   
13531  issue loading old toshiba pc software update n...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
13452                 0.980390                    POSITIVE          1  
13461                 0.744580                    POSITIVE          1  
13485                 0.983234                    POSITIVE          1  
13518                 0.541749                    POSITIVE          1  
13531                 0.998493                    POSITIVE          1

In [18]:
data_mcafee_pos_list = data_mcafee_pos["Raw_Review_Text"].values.tolist()

mcafee_pos_reviews = ' '.join([str(item) for item in data_mcafee_pos_list])

mcafee_pos_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in mcafee_pos_reviews.split(" ")])
mcafee_pos_reviews = preprocess(mcafee_pos_reviews)
mcafee_pos_reviews = remove_emojis(mcafee_pos_reviews)
mcafee_pos_reviews

'  there are  things you should be aware of when purchasing mcafee total protection . it will change your google search to yahoo. this should be easily fixed by going to google chrome setting and change it back to google search.the second is the auto renewal that should also get fixed easy by going into setting just before days from program end and not right after installing.otherwise mcafee is one of the best product there for cyber security   great product and mcafee customer service is very helpful with installation of the product. the price is better than buying from mcafee directly.   well worth the  bucks i paid! comes with a password manager and vpn. amazon gave me a generous discount over the manufacturers retail price, which was almost double. this is a good product at a reasonable price.   i have been  using mcafee for about  year and i will say that it has been the best antivirus i have ever used, and the best thing is the price way cheaper than any other store or mcafee web

In [19]:
bert_summary_mcafee_pos = ''.join(bert_model(mcafee_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all McAfee positive reviews is: \n\n\n", bert_summary_mcafee_pos)


 Text summarization of the all McAfee positive reviews is: 


 there are  things you should be aware of when purchasing mcafee total protection . the price is better than buying from mcafee directly. works great after installation! product was easy to download and install! will definitely buy this product again. its a thumbs up   great product would not be without it   like   easy to install  great price  i have not needed tech support so i do not know  i am happy so far   we prefer mcafee. you can either buy this here at a reasonable price and type in the code  minutes of your time  max or you can use the autorenewal in the companys product for an exorbitant price. not computer savvy this was easy to set up on my computer works great for current virus protection on my new used computer   have used this product for yrs now and it has lived up to its reputation. it is a great product and does everything as advertised.the internet price is significantly cheaper that the big box stores. 

## Text Summarizing the Negative sentiment McAfee reviews

In [20]:
data_mcafee_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'McAfee') ]
data_mcafee_neg = data_mcafee_neg.head(1000)
data_mcafee_neg.head()

User Name Device_Name  \
13396  S. Marshall Priddy      McAfee   
13397     Amazon Customer      McAfee   
13398       Aileen Arzate      McAfee   
13399           rat racer      McAfee   
13400             CaliGal      McAfee   

                                        Raw_Review_Title  \
13396  It's basically the same as malware in and of i...   
13397  I replaced the free versions of Avast anti-vir...   
13398                              Dont waste your money   
13399                               Good product overall   
13400                             Perfect and super easy   

                                         Raw_Review_Text  \
13396    Total waste of money.  SO SO SO obnoxious.  ...   
13397    I replaced the free versions of Avast anti-v...   
13398    I have always used mcafee but after today ne...   
13399    You do get the annoying messages from the ap...   
13400    It doesn't get better than this. From the lo...   

                                    Cleaned_Review_Title  \
13396                                  basically malware   
13397  replaced free version avast antivirus malwareb...   
13398                                   dont waste money   
13399                               good product overall   
13400                                 perfect super easy   

                                     Cleaned_Review_Text                Star  \
13396  total waste money obnoxious decided change def...  1.0 out of 5 stars   
13397  replaced free version avast antivirus malwareb...  2.0 out of 5 stars   
13398  always used mcafee today never code kept givin...  1.0 out of 5 stars   
13399  get annoying message application install anoth...  3.0 out of 5 stars   
13400  doesnt get better low price convenience perfec...  5.0 out of 5 stars   

                                      Review posted time  \
13396     Reviewed in the United States on July 24, 2018   
13397     Reviewed in the United States on July 10, 2018   
13398   Reviewed in the United States on August 10, 2018   
13399  Reviewed in the United States on November 26, ...   
13400   Reviewed in the United States on October 1, 2018   

                                       Total_Description  \
13396  total waste money obnoxious decided change def...   
13397  replaced free version avast antivirus malwareb...   
13398  always used mcafee today never code kept givin...   
13399  get annoying message application install anoth...   
13400  doesnt get better low price convenience perfec...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
13396                 0.998976                    NEGATIVE          0  
13397                 0.996654                    NEGATIVE          0  
13398                 0.998642                    NEGATIVE          0  
13399                 0.996708                    NEGATIVE          0  
13400                 0.993389                    NEGATIVE          0

In [21]:
data_mcafee_neg_list = data_mcafee_neg["Raw_Review_Text"].values.tolist()

mcafee_neg_reviews = ' '.join([str(item) for item in data_mcafee_neg_list])

mcafee_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in mcafee_neg_reviews.split(" ")])
mcafee_neg_reviews = preprocess(mcafee_neg_reviews)
mcafee_neg_reviews = remove_emojis(mcafee_neg_reviews)
mcafee_neg_reviews

'  total waste of money.  so so so obnoxious.  it decided to change my default browser to yahoo.  okay, well you can switch it back, right  sure, but it is going to nag you to reenable it on like a weekly basis.  i ended up uninstalling and regretting i ever wasted money on this.the whole point of trying to protect your computer is that i want to do what i want to do, not have pop ups, not have some software i am not trying to run steal all resources and make the things i want to do go slower.  it just ruins your computer, steals your time, runs programs you do not want at bad times, opens windows you did not ask for, and generally takes control of your computer while booting you to the role of supplicant having to ask its permission to do anything.  its got all of the bad aspects of actual malware, leaving you wondering what the point is.if anyone has a good recommendation for an antimalware packages that is not an annoying interjection all the time or a resource hogthat is, something

In [22]:
bert_summary_mcafee_neg = ''.join(bert_model(mcafee_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all McAfee negative reviews is: \n\n\n", bert_summary_mcafee_neg)


 Text summarization of the all McAfee negative reviews is: 


 it decided to change my default browser to yahoo. i have had the product for  months. the product code does not work and until this review area i have had no way to let anyone know of my problem. i will be shopping for a different antivirus, the product should have a selection for me to turn off all notifications that i do not want. i am currently using mcafee on my laptop because, in the past, it was easy to install. i chose mcafee because of their years of trust   tried more than  hours and  tries to download and install. i started a chat with tech support. mcafee could not help me and was transferred to another department that was charging me money to help with installation. nothing   product would not download to my computer. they felt like was robbed by amazon. i what to return this item from my current orders i deleted the computer that went with it   keeps computer secure   had the same thing but it expired, only i 

## Text Summarizing the Positive sentiment Nooie Baby Moniter reviews

In [23]:
data_nooie_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'Nooie Baby Moniter') ]
data_nooie_pos.head()

User Name         Device_Name  \
14744      Zichao Fu  Nooie Baby Moniter   
14749            JDS  Nooie Baby Moniter   
14751  Sandra Huizar  Nooie Baby Moniter   
14752  Sandra Huizar  Nooie Baby Moniter   
14754          Yilin  Nooie Baby Moniter   

                                        Raw_Review_Title  \
14744                  Useful to take care of my pet dog   
14749                                      Great product   
14751    Great camera, easy to set up, worth the price!!   
14752  Great size, really easy to use, good for my pets!   
14754                          Smart and powerful camera   

                                         Raw_Review_Text  \
14744    I bought the 360 because I need to check whe...   
14749    Awesome camera and quality.  I've bought 2 a...   
14751    This camera is really worth the price compar...   
14752    My pets love it! They always walk around it....   
14754    I like this camera very much. It looks simpl...   

                      Cleaned_Review_Title  \
14744             useful take care pet dog   
14749                        great product   
14751    great camera easy set worth price   
14752  great size really easy use good pet   
14754                smart powerful camera   

                                     Cleaned_Review_Text                Star  \
14744  bought 360 need check whether dog behaves well...  5.0 out of 5 stars   
14749  awesome camera quality ive bought 2 already on...  5.0 out of 5 stars   
14751  camera really worth price compare camera bough...  5.0 out of 5 stars   
14752  pet love always walk around dont need worry im...  5.0 out of 5 stars   
14754  like camera much look simple smart powerful re...  5.0 out of 5 stars   

                                      Review posted time  \
14744   Reviewed in the United States on August 17, 2019   
14749  Reviewed in the United States on October 29, 2019   
14751   Reviewed in the United States on August 25, 2019   
14752   Reviewed in the United States on August 13, 2019   
14754      Reviewed in the United States on May 13, 2019   

                                       Total_Description  \
14744  bought 360 need check whether dog behaves well...   
14749  awesome camera quality ive bought 2 already on...   
14751  camera really worth price compare camera bough...   
14752  pet love always walk around dont need worry im...   
14754  like camera much look simple smart powerful re...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
14744                 0.996608                    POSITIVE          1  
14749                 0.997728                    POSITIVE          1  
14751                 0.990433                    POSITIVE          1  
14752                 0.997399                    POSITIVE          1  
14754                 0.994250                    POSITIVE          1

In [24]:
data_nooie_pos_list = data_nooie_pos["Raw_Review_Text"].values.tolist()

nooie_pos_reviews = ' '.join([str(item) for item in data_nooie_pos_list])

nooie_pos_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in nooie_pos_reviews.split(" ")])
nooie_pos_reviews = preprocess(nooie_pos_reviews)
nooie_pos_reviews = remove_emojis(nooie_pos_reviews)
nooie_pos_reviews

'  i bought the  because i need to check whether my dog behaves well while im away. so exciting to watch and talk with her, seems like im still with her. the image quality is superb and i can even zoom in closer on the image. my dog walks around in the house and jumps to the sofa sometimes. it did follow her movement automatically thanks to its motion tracking feature. i can see her all day long. absolutely love this camera!   awesome camera and quality.  i have bought  already and one of the non moving ones as well. awesome infrared and great customer service! i will continue to use these even after my baby is grown!   this camera is really worth the price compare to the other cameras i bought before! it has great night vision feature, high picture quality and the camera can pan up and down so i can easily look around the room.  its a great indoor camera. the sound through the app is clear and the twoway audio works well, my cat tries to find me every time i talk through the camera lo

In [25]:
bert_summary_nooie_pos = ''.join(bert_model(nooie_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Nooie Baby Moniter positive reviews is: \n\n\n", bert_summary_nooie_pos)


 Text summarization of the all Nooie Baby Moniter positive reviews is: 


 i bought the  because i need to check whether my dog behaves well while im away. the setup is extremely easy the app walks you through it and the picture quality is great. i am happy with the picture and it works with the phone app. i am very impressed    we have two noovie  cameras. i also like the motion detection option because the camera moves around as my dog moves around the room but this feature can be easily turned off. i love that i can record and take pictures with it. it is a funuseful product and i intend to buy several for gifts   the camera was great the quality is really good during the day and also the night vision is better than expected. i can even use the  device to check in on my dog    very good with view and picture quality. the recording and playback feature is a nice addon. purchased this camera to keep an eye on my critters when i am out of town. i am excited to use it for my pets when 

## Text Summarizing the Negative sentiment Nooie Baby Moniter reviews

In [26]:
data_nooie_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'Nooie Baby Moniter') ]
data_nooie_neg = data_nooie_neg.head(1000)
data_nooie_neg.head()

User Name         Device_Name  \
14745      Zichao Fu  Nooie Baby Moniter   
14746  Shennanigans9  Nooie Baby Moniter   
14747         Carrie  Nooie Baby Moniter   
14748            JDS  Nooie Baby Moniter   
14750  Travis J Rudd  Nooie Baby Moniter   

                                        Raw_Review_Title  \
14745  The ONLY BABY MONITOR you NEED, Especially for...   
14746  Great camera at a great price-point and simple...   
14747  Great tool to help us keep grandma safe and se...   
14748        Donâ€™t get it, spend your money elsewhere.   
14750                        BEING WATCHED EASILY HACKED   

                                         Raw_Review_Text  \
14745    Ok let me just start out by saying OH MY GOO...   
14746    I have the Nooie 1080P indoor camera and I'v...   
14747    Especially like night vision quality! Using ...   
14748    DO NOT BUYThe only good thing, when it works...   
14750    This camera followed me around the Room and ...   

                                  Cleaned_Review_Title  \
14745               baby monitor need especially price   
14746       great camera great pricepoint simple setup   
14747  great tool help u keep grandma safe secure home   
14748                   dont get spend money elsewhere   
14750                            watched easily hacked   

                                     Cleaned_Review_Text                Star  \
14745  ok let start saying oh goodness camera amazing...  5.0 out of 5 stars   
14746  nooie 1080p indoor camera ive quite happy give...  5.0 out of 5 stars   
14747  especially like night vision quality using gra...  5.0 out of 5 stars   
14748  buythe good thing work picture greateverything...  1.0 out of 5 stars   
14750  camera followed around room took picture sitti...  1.0 out of 5 stars   

                                      Review posted time  \
14745     Reviewed in the United States on April 7, 2020   
14746      Reviewed in the United States on May 18, 2019   
14747  Reviewed in the United States on November 17, ...   
14748     Reviewed in the United States on July 22, 2019   
14750     Reviewed in the United States on July 24, 2020   

                                       Total_Description  \
14745  ok let start saying oh goodness camera amazing...   
14746  nooie 1080p indoor camera ive quite happy give...   
14747  especially like night vision quality using gra...   
14748  buythe good thing work picture greateverything...   
14750  camera followed around room took picture sitti...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
14745                 0.930007                    NEGATIVE          0  
14746                 0.933415                    NEGATIVE          0  
14747                 0.963731                    NEGATIVE          0  
14748                 0.998318                    NEGATIVE          0  
14750                 0.996737                    NEGATIVE          0

In [27]:
data_nooie_neg_list = data_nooie_neg["Raw_Review_Text"].values.tolist()

nooie_neg_reviews = ' '.join([str(item) for item in data_nooie_neg_list])

nooie_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in nooie_neg_reviews.split(" ")])
nooie_neg_reviews = preprocess(nooie_neg_reviews)
nooie_neg_reviews = remove_emojis(nooie_neg_reviews)
nooie_neg_reviews

'  ok let me just start out by saying oh my goodness is this camera amazing!!  degrees to keep a watchful eye on my babes! also, remote access so that my sweet parents can also watch her when they cant be around her hence this quarantine!the price!!!!! well worth it and reasonable! the last monitor i had was over  and it died just short of its warranty and could not be sent back. very very very pleased with this product.this product also is easy to mount! no weird angle that you need to attach to the wall then screw in the cams!! nope attach then click in the cam! wonderful!   i have the nooie p indoor camera and i have been quite happy with it so i had to give this degree model a try. it takes the features of the static camera and adds the ability to pan and tilt the camera either manually or you can enable motion tracking easily through the app. i wrote a review for the static camera and many of the features carry over including its great video quality so if you have read that review

In [28]:
bert_summary_nooie_neg = ''.join(bert_model(nooie_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Nooie Baby Moniter negative reviews is: \n\n\n", bert_summary_nooie_neg)


 Text summarization of the all Nooie Baby Moniter negative reviews is: 


 ok let me just start out by saying oh my goodness is this camera amazing!! i reached out to the manufacturer via their customer service site. we planned to put this camera in our babys room which is  wall away from the router. i do not talk softly so the built in speaker is a negative for me. the puppy was seeing the light come on and that would gain her interest...also a great feature if you use it for a security camera, which we will when the puppy is grown. i only purchased it because it came up in the search for a baby monitor  it is in actuality, an indoor security camera similar to a ring but no where near as good. but it gives a motion sensor alert to the tv and the cat walking by. its also great to know when hes asleep so i dont open the door and wake him up. everything else is great about this camera. i will definately be getting another one and am looking at their outdoor camera as well! it is a great

## Text Summarizing the Positive sentiment Ring Spotlight reviews

In [29]:
data_ring_pos = reviews[(reviews.sentiment ==1) & (reviews.Device_Name == 'Ring Spotlight') ]
data_ring_pos.head()

User Name     Device_Name              Raw_Review_Title  \
19630      Michael  Ring Spotlight          Security and Safety!   
19640  Avid Reader  Ring Spotlight      New Camera, New Update!!   
19648  YogaDesires  Ring Spotlight   Great product for any home!   
19694   Steven Sun  Ring Spotlight  Good camera with some issues   
19752      Chris G  Ring Spotlight      Two tidbits, works great   

                                         Raw_Review_Text  \
19630                      The media could not be loa...   
19640    Updated Review:Received a new camera from Ri...   
19648    I definitely like this product overall as we...   
19694    I really have enjoyed having this Ring Spotl...   
19752    Works pretty well. I wanted to highlight two...   

        Cleaned_Review_Title  \
19630        security safety   
19640  new camera new update   
19648     great product home   
19694      good camera issue   
19752  two tidbit work great   

                                     Cleaned_Review_Text                Star  \
19630  medium could loaded wow idea much happens outs...  5.0 out of 5 stars   
19640  updated reviewreceived new camera ring setup p...  5.0 out of 5 stars   
19648  definitely like product overall well ring door...  4.0 out of 5 stars   
19694  really enjoyed ring spotlight camera easy set ...  4.0 out of 5 stars   
19752  work pretty well wanted highlight two thing li...  5.0 out of 5 stars   

                                      Review posted time  \
19630      Reviewed in the United States on July 2, 2018   
19640     Reviewed in the United States on April 7, 2018   
19648   Reviewed in the United States on October 4, 2018   
19694   Reviewed in the United States on August 16, 2018   
19752  Reviewed in the United States on September 11,...   

                                       Total_Description  \
19630  medium could loaded wow idea much happens outs...   
19640  updated reviewreceived new camera ring setup p...   
19648  definitely like product overall well ring door...   
19694  really enjoyed ring spotlight camera easy set ...   
19752  work pretty well wanted highlight two thing li...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
19630                 0.881575                    POSITIVE          1  
19640                 0.701090                    POSITIVE          1  
19648                 0.865335                    POSITIVE          1  
19694                 0.797928                    POSITIVE          1  
19752                 0.971783                    POSITIVE          1

In [30]:
data_ring_pos_list = data_ring_pos["Raw_Review_Text"].values.tolist()

ring_pos_reviews = ' '.join([str(item) for item in data_ring_pos_list])

ring_pos_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in ring_pos_reviews.split(" ")])
ring_pos_reviews = preprocess(ring_pos_reviews)
ring_pos_reviews = remove_emojis(ring_pos_reviews)
ring_pos_reviews

'                    the media could not be loaded.                  wow!  i had no idea so much happens outside my front door!  weve captured deer, birds building nests in my door wreath, a fox trying to get in the front door and even raccoons and stray cats wandering on our front porch, not to mention our guests whom i can speak to from other locations. if someone is up to no good, i can sound the alarm from my cell phone. we also can monitor the live feed from our alexa. we upgraded and purchased the yearly subscription to save all our videos.  with two batteries it lasts well over a month of charge.  this camera works great and is very responsive. the angle of recording is large enough to capture almost .  we purchased a second camera to cover our pool and added solar panels to keep it charged. it is great at capturing motion before anyone gets even close to the pool. great when you have little ones or pets who somehow always find ways to go where they are not suppose to.   updated

In [31]:
bert_summary_ring_pos = ''.join(bert_model(ring_pos_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Nooie Baby Moniter positive reviews is: \n\n\n", bert_summary_ring_pos)


 Text summarization of the all Nooie Baby Moniter positive reviews is: 


 i had no idea so much happens outside my front door! i have been able to see the image well and the video are usually pretty clear.my main issue is how long the batteries last. like others, the volume on the camera needs to be louder  you cannot hear unless standing right by it, but all in all we are happy. i got it to protect my cars and the community mailbox. you can adjust the range of motion the camera looks at and notifies about.i love the neighborhood features and am looking forward to more features and how this network will grow. rings app works really well with both cameras too allowing me to set two different sounds for motion alerts so i know which camera is alarming. both camera and solar panel are real easy to install. the spotlight is led so it is very bright. light is good but not overpowering. the customer service part is why i give it a one star. was easy to install and has  adequate lighting wi

## Text Summarizing the Negative sentiment Ring Spotlight reviews

In [32]:
data_ring_neg = reviews[(reviews.sentiment ==0) & (reviews.Device_Name == 'Ring Spotlight') ]
data_ring_neg = data_ring_neg.head(1000)
data_ring_neg.head()

User Name     Device_Name  \
19628     ArikB  Ring Spotlight   
19629   Michael  Ring Spotlight   
19631     Donna  Ring Spotlight   
19632       LGG  Ring Spotlight   
19633     Jamie  Ring Spotlight   

                                        Raw_Review_Title  \
19628  Very Good Security Camera, Please Read If Disc...   
19629         Super Easy to Install, no wires necessary!   
19631            Inaccurate at times, but still workable   
19632  The camera didnâ€™t work very well at all. Whe...   
19633  Inferior to Arlo, I'll give it a little more time   

                                         Raw_Review_Text  \
19628    I read many of the reviews and almost did no...   
19629    I have a Ring pro on my front door and loved...   
19631    I've previously owned Arlo security cameras,...   
19632    The camera didnâ€™t work very well at all. W...   
19633    So, got this battery model to see if it woul...   

                                    Cleaned_Review_Title  \
19628  good security camera please read discouraged a...   
19629                  super easy install wire necessary   
19631                     inaccurate time still workable   
19632                             camera didnt work well   
19633                 inferior arlo ill give little time   

                                     Cleaned_Review_Text                Star  \
19628  read many review almost purchase camera howeve...  4.0 out of 5 stars   
19629  ring pro front door loved much wanted somethin...  5.0 out of 5 stars   
19631  ive previously owned arlo security camera ring...  3.0 out of 5 stars   
19632  camera didnt work well motion sensor turned wo...  1.0 out of 5 stars   
19633  got battery model see would work well arlo pro...  1.0 out of 5 stars   

                                      Review posted time  \
19628  Reviewed in the United States on November 25, ...   
19629     Reviewed in the United States on April 1, 2018   
19631    Reviewed in the United States on April 25, 2018   
19632      Reviewed in the United States on May 16, 2018   
19633  Reviewed in the United States on September 9, ...   

                                       Total_Description  \
19628  read many review almost purchase camera howeve...   
19629  ring pro front door loved much wanted somethin...   
19631  ive previously owned arlo security camera ring...   
19632  camera didnt work well motion sensor turned wo...   
19633  got battery model see would work well arlo pro...   

       ReviewDescription_score ReviewDescription_Sentiment  sentiment  
19628                 0.988290                    NEGATIVE          0  
19629                 0.968418                    NEGATIVE          0  
19631                 0.996341                    NEGATIVE          0  
19632                 0.998062                    NEGATIVE          0  
19633                 0.999449                    NEGATIVE          0

In [33]:
data_ring_neg_list = data_ring_neg["Raw_Review_Text"].values.tolist()

ring_neg_reviews = ' '.join([str(item) for item in data_ring_neg_list])

ring_neg_reviews = ' '.join([contraction_mapping[t] if t in contraction_mapping else t for t in ring_neg_reviews.split(" ")])
ring_neg_reviews = preprocess(ring_neg_reviews)
ring_neg_reviews = remove_emojis(ring_neg_reviews)
ring_neg_reviews

'  i read many of the reviews and almost did not purchase the camera because of them. however, after making the decision to buy two and using them for the past  weeks, i have been very pleased. prior to my purchase i owned a ring doorbell, and since i have purchased a ring floodlight cam. all of my cameras work extremely well.i wanted to address the comments some people are making about these cameras as i think they are a little inaccurate. the battery life is not poor. i have two cameras on the back of my house and they ran on the original battery for  weeks. to ease concerns about poor battery life, i have had my cameras set on the standard motion detection setting and  weeks is pretty good. additionally, each camera holds two batteries so ideally you can get up to  weeks without changing the batteries at all. we have a lot of deers, rabbits, etc in addition to our dog so our motions probably go off more than the average household.as far as video quality, these work well at night and

In [34]:
bert_summary_ring_neg = ''.join(bert_model(ring_neg_reviews, max_length = 200, min_length=30, num_sentences = 20))
print ("\n Text summarization of the all Ring Spotlight negative reviews is: \n\n\n", bert_summary_ring_neg)


 Text summarization of the all Ring Spotlight negative reviews is: 


 i read many of the reviews and almost did not purchase the camera because of them. we have a lot of deers, rabbits, etc in addition to our dog so our motions probably go off more than the average household.as far as video quality, these work well at night and in the day. all in all if you have a way to install the wired camera, go that route as you will be happier with the camera features and video quality. i have highspeed spectrum internet and good speed all over my property. ive stopped emailing and calling ring tech support because all they do is blame those two things.i like having a visible camera to deter unwanted individuals. i am adding two more around the house. i have comcast gig internet and the camera is no more  feet away. you can adjust the sensing range though, and after i fixed it, it will detect you from further out. also, the ball mount seems very weak. if you want a camera that records all the t